In [1]:
import numpy as np
import math
import IPython.display as ipd
import librosa
import librosa.display
import pycwt
import soundfile as sf
import io
from google.cloud import storage
import os
import tensorflow as tf
import tensorflow.io.gfile as gf
import matplotlib.pyplot as plt 
import skimage.io
import muda
import jams
import threading

In [2]:
mutex = threading.Lock()

In [3]:
def Noise(fp):
    mutex.acquire()
    J = muda.load_jam_audio(jams.JAMS(), fp)
    mutex.release()
    x = J.sandbox.muda._audio['y']
    Fs = J.sandbox.muda._audio['sr']
    dur=librosa.get_duration(x,Fs)
    if(dur<.98):
        return
    if(dur>1.02):
        return
    D=muda.deformers.BackgroundNoise(n_samples=1, files=r"C:\Users\jayoj\Downloads\audiocheck.net_whitenoise.wav", weight_min=0.05000, weight_max=0.05000000001)
    JN=D.transform(J)
    J2=next(JN)
    y = J2.sandbox.muda._audio['y']
    Fs = J2.sandbox.muda._audio['sr']
    return [y,Fs]

def TimeS(fp):
    mutex.acquire()
    J = muda.load_jam_audio(jams.JAMS(), fp,duration=0.5)
    mutex.release()
    x = J.sandbox.muda._audio['y']
    Fs = J.sandbox.muda._audio['sr']
    dur=librosa.get_duration(x,Fs)
    if(dur<.98):
        return
    D = muda.deformers.TimeStretch(rate=0.5)
    JN=D.transform(J)
    J2=next(JN)
    y = J2.sandbox.muda._audio['y']
    Fs = J2.sandbox.muda._audio['sr']
    return [y,Fs]

def Pitch(fp):
    mutex.acquire()
    J = muda.load_jam_audio(jams.JAMS(), fp)
    mutex.release()
    x = J.sandbox.muda._audio['y']
    Fs = J.sandbox.muda._audio['sr']
    dur=librosa.get_duration(x,Fs)
    if(dur<.98):
        return
    D = muda.deformers.PitchShift(n_semitones=-0.5)
    JN=D.transform(J)
    print(JN)
    J2=next(JN)
    y = J2.sandbox.muda._audio['y']
    Fs = J2.sandbox.muda._audio['sr']
    return [y,Fs]

#sf.write("testTime.wav", y, Fs)

In [4]:
def ThreadFunc(aug):
    global index
    global L
    while(index<len(L)):
        mutex.acquire()
        spot=index
        index=index+1
        mutex.release()
        if(aug=="Noise"):
            [y,Fs]=Noise(L[spot])
            out=L[spot].replace("sec","Noise")  
        elif(aug=="Stretch"):
            [y,Fs]= TimeS(L[spot])
        elif(aug=="Pitch"):
            [y,Fs]=Pitch(L[spot])
        
        
        mutex.acquire()     
        
        d= out[0:(int)(out.rfind("\\"))]
        if not os.path.exists(d):
            try:
                os.makedirs(d)
            except:
                print("oops")
        sf.write(out, y, Fs)
        
        print(out)
        mutex.release()
            
    

In [5]:
L=[]
index=0
root=r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1sec"
for path, subdirs, files in os.walk(root):
    for name in files:
        L.append(os.path.join(path, name))
        

x=[]
for i in range(1,25):
    T=threading.Thread(target=ThreadFunc,args=("Noise",),daemon=True)
    T.name=str(i)
    x.append(T)
    T.start()
  
for th in x:    
    th.join()

Exception in thread 1:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object
Exception in thread 2:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object
Exception in thread 12:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture102.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture100.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture101.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture103.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture08.wav

Exception in thread 16:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object



C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture106.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture108.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture116.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture109.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture111.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture107.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture115.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\001\mixture110.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixt

Exception in thread 4:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object


...


C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture100.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture101.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture102.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture103.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture104.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture106.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture107.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture108.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture109.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture110.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mi

Exception in thread 17:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object


C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture121.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture122.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture123.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture124.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture125.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture126.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture127.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture128.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture129.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture130.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mix

Exception in thread 24:
Traceback (most recent call last):
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "C:\Users\jayoj\anaconda3\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-4-8fcb6be2a4e1>", line 10, in ThreadFunc
TypeError: cannot unpack non-iterable NoneType object



C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture133.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_1Noise\Mixtures\002\mixture134.wav


In [11]:
root=r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Tet"


for path, subdirs, files in os.walk(root):
    for name in files:
        if 'wav' in os.path.join(path, name):
            print(os.path.join(path, name))
            [y,Fs]=Noise(os.path.join(path, name))
            sf.write(os.path.join(path, name), y, Fs)
            

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\001\bass11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\S

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\002\bass23.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\S

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other23.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other24.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\003\other25.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\004\drums21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\005\other16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

...

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\047\vocals40.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\047\vocals41.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\047\vocals42.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\bass08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5N

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other23.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other24.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other25.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other26.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\048\other27.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\049\drums12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\bass12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\S

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other11.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other12.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Noise\Sources\Test\050\other22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD

In [29]:
print(r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5sec\Mixtures\Dev\051\mixture00.wav")
c=r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture00.wav"
c=c.replace("DSD100_5sec","DSD100_5Stretch")
d= c.rfind("\\")
d= c[0:(int)(c.rfind("\\"))]
print(d)
print(c)
#sf.write(r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture00.wav", y, Fs)
#os.makedirs(r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture00.wav")

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5sec\Mixtures\Dev\051\mixture00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture00.wav


In [31]:
root=r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5sec"
for path, subdirs, files in os.walk(root):
    for name in files:
        if 'wav' in os.path.join(path, name):
            c=os.path.join(path, name)
            c=c.replace("DSD100_5sec","DSD100_5Stretch")
            print(c)
            [y,Fs]=TimeS(os.path.join(path, name))
            
            d= c[0:(int)(c.rfind("\\"))]
            if not os.path.exists(d):
                os.makedirs(d)
            sf.write(c, y, Fs)

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixture10.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\051\mixtur

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture13.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture14.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixture23.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\053\mixtur

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\055\mixture35.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture06.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture07.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture08.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixture09.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\056\mixtur

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture53.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture54.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture55.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture56.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture57.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture58.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture59.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture60.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture61.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture62.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixture63.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\057\mixtur

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture32.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture33.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture34.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture35.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture36.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture37.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture38.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture39.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture40.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture41.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixture42.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Mixtures\Dev\059\mixtur

...

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other15.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other16.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other17.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other18.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other19.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other20.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other21.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other22.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other23.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other24.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other25.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\047\other26.wav
C:\Users\jayoj\D

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass30.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass31.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass32.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass33.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass34.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass35.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass36.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass37.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass38.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass39.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass40.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\048\bass41.wav
C:\Users\jayoj\Documents\GT\

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\drums29.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\drums30.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\drums31.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\drums32.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\drums33.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other00.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other01.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other02.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other03.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other04.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other05.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\049\other06.wav
C:\Users\jayoj\D

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass27.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass28.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass29.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass30.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass31.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass32.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass33.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass34.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass35.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass36.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass37.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\bass38.wav
C:\Users\jayoj\Documents\GT\

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other35.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other36.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other37.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other38.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other39.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other40.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other41.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other42.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other43.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other44.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other45.wav
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Stretch\Sources\Test\050\other46.wav
C:\Users\jayoj\D

In [32]:
root=r"C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5sec"
for path, subdirs, files in os.walk(root):
    for name in files:
        if 'wav' in os.path.join(path, name):
            c=os.path.join(path, name)
            c=c.replace("DSD100_5sec","DSD100_5Pitch")
            print(c)
            [y,Fs]=Pitch(os.path.join(path, name))
            
            d= c[0:(int)(c.rfind("\\"))]
            if not os.path.exists(d):
                os.makedirs(d)
            sf.write(c, y, Fs)

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture00.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture01.wav
<generator object BaseTransformer.transform at 0x0000020F166EE430>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture02.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture03.wav
<generator object BaseTransformer.transform at 0x0000020F166EE430>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture04.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture05.wav
<generator object BaseTransformer.transform at 0x0000020F166EE430>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\051\mixture06.wav
<generator object BaseTr

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture12.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture13.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture14.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture15.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture16.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture17.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\052\mixture18.wav
<generator object BaseTr

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture25.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture26.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture27.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture28.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture29.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture30.wav
<generator object BaseTransformer.transform at 0x0000020F16710EB0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\053\mixture31.wav
<generator object BaseTr

C:\Users\jayoj\anaconda3\lib\site-packages\librosa\core\pitch.py:153: UserWarning: Trying to estimate tuning from empty frequency set.
  warnings.warn("Trying to estimate tuning from empty frequency set.")



C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture01.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture02.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture03.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture04.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture05.wav
<generator object BaseTransformer.transform at 0x0000020F16921120>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture06.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Mixtures\Dev\055\mixture07.wav
<generator object BaseT

...

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\bass29.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\bass30.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\bass31.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\bass32.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\bass33.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\drums00.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\drums01.wav
<generator object BaseTransformer.transform

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other17.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other18.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other19.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other20.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other21.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other22.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\049\other23.wav
<generator object BaseTransformer.tran

C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass05.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass06.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass07.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass08.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass09.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass10.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\bass11.wav
<generator object BaseTransformer.transform a

<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums15.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums16.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums17.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums18.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums19.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\drums20.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\

<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other24.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other25.wav
<generator object BaseTransformer.transform at 0x0000020F166EEBA0>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other26.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other27.wav
<generator object BaseTransformer.transform at 0x0000020F166EE040>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other28.wav
<generator object BaseTransformer.transform at 0x0000020F166EE970>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\Sources\Test\050\other29.wav
<generator object BaseTransformer.transform at 0x0000020F166EE200>
C:\Users\jayoj\Documents\GT\SML\Data\DSD100_5Pitch\

Archived code:

In [5]:
#Noise introduction
J = muda.load_jam_audio(jams.JAMS(), r"C:\Users\jayoj\Documents\GT\SML\Data\Test\NewsTest2.wav",duration=10)
x = J.sandbox.muda._audio['y']
Fs = J.sandbox.muda._audio['sr']
D=muda.deformers.BackgroundNoise(n_samples=1, files=r"C:\Users\jayoj\Downloads\audiocheck.net_whitenoise.wav", weight_min=0.05000, weight_max=0.05000000001)
JN=D.transform(J)
J2=next(JN)
y = J2.sandbox.muda._audio['y']
Fs = J2.sandbox.muda._audio['sr']
sf.write("testBGN.wav", y, Fs)

In [10]:
#Time stretch 

[y,Fs]=TimeS(r"C:\Users\jayoj\Documents\GT\SML\Data\Test\NewsTest2.wav")

sf.write("testTime.wav", y, Fs)




In [17]:
#Pitch shifting

J = muda.load_jam_audio(jams.JAMS(), r"C:\Users\jayoj\Documents\GT\SML\Data\Test\NewsTest2.wav",duration=10)
x = J.sandbox.muda._audio['y']
Fs = J.sandbox.muda._audio['sr']
D = muda.deformers.PitchShift(n_semitones=-0.5)

JN=D.transform(J)
print(JN)
J2=next(JN)
y = J2.sandbox.muda._audio['y']
Fs = J2.sandbox.muda._audio['sr']
sf.write("testPitch.wav", y, Fs)



<generator object BaseTransformer.transform at 0x000002AF270A2970>


In [20]:
#DRC (Bugged)

J = muda.load_jam_audio(jams.JAMS(), r"C:\Users\jayoj\Documents\GT\SML\Data\Test\NewsTest2.wav",duration=10)
x = J.sandbox.muda._audio['y']
Fs = J.sandbox.muda._audio['sr']
D = muda.deformers.DynamicRangeCompression(preset=muda.deformers.PRESETS.keys())
JN=D.transform(J)
print(JN)
print(J)
J2=next(JN)
y = J2.sandbox.muda._audio['y']
Fs = J2.sandbox.muda._audio['sr']
sf.write("testDRC.wav", y, Fs)


<generator object BaseTransformer.transform at 0x000002AF271377B0>
{
  "annotations": [],
  "file_metadata": {
    "title": "",
    "artist": "",
    "release": "",
    "duration": 10.0,
    "identifiers": {},
    "jams_version": "0.3.4"
  },
  "sandbox": {
    "muda": {
      "history": [],
      "state": [],
      "version": {
        "muda": "0.4.1",
        "librosa": "0.8.0",
        "jams": "0.3.4",
        "pysoundfile": "0.9.0"
      }
    }
  }
}


FileNotFoundError: [WinError 2] The system cannot find the file specified